# Bajada de datos

El siguiente notebook sirve para obtener los datos desde la api de python de Google Earth engine (GEE). ESta es una copia del Notebook anterioor el proiblema es que hay bandas que no se estan generando y no se cual es el problema. 


In [ ]:
import ee
import geemap
import folium
import os 
import rasterio
import numpy as np
import requests 
import zipfile
import time

In [ ]:
ee.Authenticate()

Enter verification code:  4/1Adeu5BUUpjah8MxeAVeTKrWXub2eBFxxuKZ6IYOT3g8BtRGb2-5LrZEDIn8



Successfully saved authorization token.


In [ ]:
ee.Initialize()


In [ ]:
#| export
def humedad_relativa(image):
    # Se utiliza la siguiente formula 
      # e = 6.1078 *math.exp((17.1*Tem_dew)/(235+Tem_dew) )
      # e_s = 6.1078 *math.exp((17.1*Temp)/(235+Temp) )
      # HR = (e/e_s)*100
   
    lambda_i = 240.97
    beta_i = 17.502 #### #17.1; #17.625;
    coef= 611.21; ####// reference level water vapor pressure at 273.15 K
    dew_point =  image.select('dewpoint_temperature_2m')
    temp_2m =  image.select('temperature_2m')
    evap = image.select('total_evaporation')
    tot_pre_h = image.select('total_precipitation_hourly')
    tot_pre = image.select('total_precipitation')
    e_up  =  dew_point.multiply(beta_i)
    e_dow =   dew_point.add(lambda_i)
    e = ((e_up.divide(e_dow)).exp()).multiply(coef)
    e_s_up  =  temp_2m.multiply(beta_i)
    e_s_dow =   temp_2m.add(lambda_i);
    e_s   = ((e_s_up.divide(e_s_dow)).exp()).multiply(coef);
    rel_hum = (e.divide(e_s)).multiply(100);
    
    rel_hum = rel_hum.select(['dewpoint_temperature_2m']).rename(['relative_humidity']);
      
    evap_mul = evap.multiply(lambda_i);
    tot_pre_h_mul = tot_pre_h.multiply(beta_i);
    tot_pre_mul =   tot_pre.multiply(coef);
    tonteria = (evap_mul.add(tot_pre_h_mul)).add(tot_pre_mul)
    tonteria = tonteria.select(['total_evaporation']).rename(['tonteria']);
    rel_hum.select(['dewpoint_temperature_2m']).rename(['relative_humidity']);
    
    image = image.addBands([rel_hum, tonteria]);
    
    return image


In [ ]:
def  get_image_raster_mean(collection, start_date, end_date):
    
    
    numberOfDays = end_date.difference(start_date, 'days')
    lapse = ee.List.sequence(0, numberOfDays.subtract(1)) 
    def next_day(day):
        return ee.Date(start_date).advance(day, 'day')
    
    listdates = lapse.map(next_day)
    def mean_day(day):
        day_collection = collection.filter(ee.Filter.date(day,ee.Date(day).advance(1, 'day') ))
        mean_day=  day_collection.mean();
        mean_day= mean_day.set('day' , day)
        return mean_day
    
    image_means = listdates.map(mean_day)
    
    return ee.ImageCollection(image_means);



In [ ]:

def ima_land_reproject (image_col, reproject_pro ):
    return ee.Image(image_col).resample('bilinear').reproject(crs= reproject_pro, scale=926.625 )
    #return ee.Image(image_col).reproject(crs= proj_, scale=926.625 )

    
    
def ima_land_reproject_no_resample(image_col, reproject_pro ):
    return ee.Image(image_col).reproject(crs= reproject_pro, scale=926.625 )
    #return ee.Image(image_col).reproject(crs= proj_, scale=926.625 )
    


In [ ]:
def get_image_range_LST(start_Date, end_Date, get_zm):
    """
    
    """
    range_all_images = ee.DateRange(start_Date, end_Date)# Rango de dias
    difference_days = range_all_images.end().difference(range_all_images.start() , 'day')
    #todos los dias como una secuencia
    
    bb_get_zm = get_zm.geometry().bounds()
    #print(bb_get_zm.getInfo())
    def clip_zm_fun(img):
        return img.clip(bb_get_zm)
    
    Modis_LST =  ee.ImageCollection("MODIS/061/MOD11A1").filter(
        ee.Filter.date(start_Date, end_Date)
        ).map(clip_zm_fun)
    proje_pro = get_zm.first().geometry().projection()
    
    def ima_land_reproject_wrap(image):
        return ima_land_reproject_no_resample(image,proje_pro)
    Modis_LST = Modis_LST.map(ima_land_reproject_wrap)
    
    return Modis_LST


In [ ]:
#| export 
def get_image_range(start_Date, end_Date, get_zm ):
    """
    Get a image collection with AOD and meteorogical data on the images
    """
    
    range_all_images = ee.DateRange(start_Date, end_Date)# Rango de dias
    difference_days = range_all_images.end().difference(range_all_images.start() , 'day')
    #todos los dias como una secuencia
    
    bb_get_zm = get_zm.geometry().bounds()
    #print(bb_get_zm.getInfo())
    def clip_zm_fun(img):
        return img.clip(bb_get_zm)
    
    land_eras_day_f = ee.ImageCollection("ECMWF/ERA5_LAND/HOURLY").filter(
            ee.Filter.date(start_Date, end_Date)
        ).select([
            'dewpoint_temperature_2m',
            'total_evaporation',
            'temperature_2m',
            'total_precipitation_hourly',
            'total_precipitation'
        ]).map(clip_zm_fun)
    
    AOD_MODIS_day_f =  ee.ImageCollection("MODIS/006/MCD19A2_GRANULES").filter(
        ee.Filter.date(start_Date, end_Date)
        ).select([
            'Optical_Depth_047',
            'AOD_Uncertainty'
        ]).map(clip_zm_fun)
    
    proje_pro = get_zm.first().geometry().projection()
    
    def ima_land_reproject_wrap(image):
        return ima_land_reproject(image,proje_pro)
    
    def ima_land_no_reproject_wrap(image):
        return ima_land_reproject_no_resample(image,proje_pro)
    
    
    land_eras_day_f = land_eras_day_f.map(humedad_relativa)
    land_eras_day_f = get_image_raster_mean(land_eras_day_f, start_Date, end_Date)
    land_eras_day_f = land_eras_day_f.map(ima_land_reproject_wrap)
    
    AOD_MODIS_day_f = get_image_raster_mean(AOD_MODIS_day_f,start_Date, end_Date)
    AOD_MODIS_day_f = AOD_MODIS_day_f.map(ima_land_no_reproject_wrap)
    
    
    
    
    
    ##### Se unen las collecciones 
    filter_maps = ee.Filter.equals(leftField= 'day',rightField= 'day')
    simpleJoin = ee.Join.inner()
    innerJoin = ee.ImageCollection(simpleJoin.apply(land_eras_day_f, AOD_MODIS_day_f, filter_maps))
    
    def cat_fun(feature):
        return ee.Image.cat(feature.get('primary'), feature.get('secondary'))
    
    
    joined_aod_tem = innerJoin.map(cat_fun)
    joined_aod_tem = joined_aod_tem.map(clip_zm_fun)
    joined_aod_tem = joined_aod_tem.select([
                  "dewpoint_temperature_2m",
                  "total_evaporation",
                  "temperature_2m",
                  "total_precipitation_hourly",
                  "total_precipitation",
                  "relative_humidity",
                  "Optical_Depth_047",
                  "AOD_Uncertainty", 
                  "tonteria"
                ])
    return joined_aod_tem


In [ ]:
#| export 
def get_image_range_no_resample(start_Date, end_Date, get_zm ):
    """
    Get a image collection with AOD and meteorogical data on the images
    """
    
    range_all_images = ee.DateRange(start_Date, end_Date)# Rango de dias
    difference_days = range_all_images.end().difference(range_all_images.start() , 'day')
    #todos los dias como una secuencia
    
    bb_get_zm = get_zm.geometry().bounds()
    #print(bb_get_zm.getInfo())
    def clip_zm_fun(img):
        return img.clip(bb_get_zm)
    
    land_eras_day_f = ee.ImageCollection("ECMWF/ERA5_LAND/HOURLY").filter(
            ee.Filter.date(start_Date, end_Date)
        ).select([
            'dewpoint_temperature_2m',
            'total_evaporation',
            'temperature_2m',
            'total_precipitation_hourly',
            'total_precipitation'
        ]).map(clip_zm_fun)
    
    AOD_MODIS_day_f =  ee.ImageCollection("MODIS/006/MCD19A2_GRANULES").filter(
        ee.Filter.date(start_Date, end_Date)
        ).select([
            'Optical_Depth_047',
            'AOD_Uncertainty'
        ]).map(clip_zm_fun)
    
    proje_pro = get_zm.first().geometry().projection()
    
    def ima_land_reproject_wrap(image):
        return ima_land_reproject(image,proje_pro)
    
        return ima_land_reproject_no_resample(image,proje_pro)
    
    
    land_eras_day_f = land_eras_day_f.map(humedad_relativa)
    land_eras_day_f = get_image_raster_mean(land_eras_day_f, start_Date, end_Date)
    land_eras_day_f = land_eras_day_f.map(ima_land_no_reproject_wrap)
    
    AOD_MODIS_day_f = get_image_raster_mean(AOD_MODIS_day_f,start_Date, end_Date)
    AOD_MODIS_day_f = AOD_MODIS_day_f.map(ima_land_no_reproject_wrap)
    
    
    
    
    
    ##### Se unen las collecciones 
    filter_maps = ee.Filter.equals(leftField= 'day',rightField= 'day')
    simpleJoin = ee.Join.inner()
    innerJoin = ee.ImageCollection(simpleJoin.apply(land_eras_day_f, AOD_MODIS_day_f, filter_maps))
    
    def cat_fun(feature):
        return ee.Image.cat(feature.get('primary'), feature.get('secondary'))
    
    
    joined_aod_tem = innerJoin.map(cat_fun)
    joined_aod_tem = joined_aod_tem.map(clip_zm_fun)
    joined_aod_tem = joined_aod_tem.select([
                  "dewpoint_temperature_2m",
                  "total_evaporation",
                  "temperature_2m",
                  "total_precipitation_hourly",
                  "total_precipitation",
                  "relative_humidity",
                  "Optical_Depth_047",
                  "AOD_Uncertainty", 
                  "tonteria"
                ])
    return joined_aod_tem

In [ ]:
dic_met_area = {
                    'ZMVM': "users/msalazar_cgeo/ZMVM",
                    'ZMG': "users/msalazar_cgeo/ZMG",
                    'ZMVT':"users/msalazar_cgeo/ZMVT",
                    'AMM': "users/msalazar_cgeo/AMM"}
ZM_table = ee.FeatureCollection(dic_met_area['ZMVM'])
startdate_fun = ee.Date("2004-01-21" )
enddate_fun = ee.Date("2004-01-22")
merge_join_col = get_image_range(startdate_fun, enddate_fun, ZM_table)

In [ ]:
get_year_zm("2004-01-21", "2004-01-22", "ZMVM",'./datos/raster/Raster_test/' )



['aod_cli_ZMVM_2004_01_21']
Total number of images: 1

Exporting 1/1: ./datos/raster/Raster_test/aod_cli_ZMVM_2004_01_21.tif
Generating URL ...
Please wait ...
Data downloaded to /mnt/HDD2/Cgeo/Contaminantes/pm-2.5_Drive/datos/raster/Raster_test/aod_cli_ZMVM_2004_01_21.tif




In [ ]:
def bands_change_nan(file_path):
    """The function chenche the value of mask for np.nan"""
    src = rasterio.open(file_path, 'r+')
    
    for band_num in range(1,src.meta['count'] +1 ):
        band_arr = src.read(band_num)
        band_arr[band_arr==-100] = np.nan
        src.write(band_arr,band_num)
    src.close()    

bands_change_nan("/home/miguel/Part1/HDD2/Cgeo/Contaminantes/pm-2.5_Drive/datos/raster/Raster_test/aod_cli_ZMVM_2004_01_21.tif")

Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


In [ ]:
url_imag = merge_join_col.first().unmask(-10000).getDownloadUrl({
    'bands': ["dewpoint_temperature_2m",
                  "total_evaporation",
                  "temperature_2m",
                  "total_precipitation_hourly",
                  "total_precipitation",
                  "relative_humidity",
                  "Optical_Depth_047",
                  "AOD_Uncertainty"
                  ],
    'format': "GEO_TIFF"
})
file_name_d_image =  ("./datos/raster/Raster_test/aod_cli_ZMVM_2004_01_21.tif")


In [ ]:
url_imag

'https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/64785547a7fc8f21adae64544f38e11c-bb8efa09f3900632953eae7e05b3abbc:getPixels'

In [ ]:
r= requests.get(url_imag, stream=True, timeout=300)
with open(file_name_d_image, "wb") as fd:
    for chunk in r.iter_content(chunk_size=1024):
        fd.write(chunk)

In [ ]:
def get_geo_tif(image,
                file_name_tif,
                unmask_val = -100, 
                url_params = None,
                re_fill_nan = True,
                timeout=300):
    """Save the image as geotiff"""
    
    if url_params is None:
        url_params =  {
            'bands': [
              "dewpoint_temperature_2m",
              "total_evaporation",
              "temperature_2m",
              "total_precipitation_hourly",
              "total_precipitation",
              "relative_humidity",
              "Optical_Depth_047",
              "AOD_Uncertainty"
            ],
            'format': "GEO_TIFF"
            }
    
    try:
        url_image = image.unmask(unmask_val).getDownloadUrl(url_params)
    except Exception as e:
        print("An error occurred while downloading.")
        print(e)
        return
    print('getting url: \n', url_image)
    r= requests.get(url_image, stream=True, timeout=timeout)
    if r.status_code != 200:
        print("An error occurred while downloading.")
        return
    
    print('Saving at : \n', file_name_tif)
    with open(file_name_tif, "wb") as fd:
        for chunk in r.iter_content(chunk_size=1024):
            fd.write(chunk)
        fd.close()
    
    
    if re_fill_nan:
        print("Fill values with Nan")
        bands_change_nan(file_name_tif)
    
    
    return 


In [ ]:
get_geo_tif(merge_join_col.first(), './datos/raster/Raster_test/single_exctract_2.tif', url_params=        url_params= {'format':"GEO_TIFF"})

getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/a94b859fb22e6e138037f0250cd0ffe0-d81a7b794eb8d7d55e71dc8cd1a2bbe1:getPixels
Saving at : 
 ./datos/raster/Raster_test/single_exctract_2.tif
Fill values with Nan


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


In [ ]:
def get_geo_collection(gee_collection, 
                       path, 
                       file_names, 
                       unmask_value= -100,
                       re_fill_nan= True,
                       timeout=300,
                       ):
    """Funcion to get all the collection"""
    count = int(gee_collection.size().getInfo())

    if file_names is None:
        file_names = ee_object.aggregate_array("system:index").getInfo()
        
    elif isinstance(file_names, int):
        file_names = [str(f + file_names) for f in range(0, count)]
    
    if len(file_names) != count:
        raise Exception(
            "The number of filenames must be equal to the number of images."
        )
    file_names = [str(f) + ".tif" for f in file_names if not str(f).endswith(".tif")]
    
    for i in range(0, count):
        image = ee.Image(gee_collection.toList(count).get(i))
        filename = os.path.join(path, file_names[i])
        print(f"Exporting {i + 1}/{count}: {filename}")
        get_geo_tif(
            image,
            file_name_tif = filename,
            unmask_val = unmask_value,
            re_fill_nan = re_fill_nan,
            timeout = timeout
        )
        print("\n")


In [ ]:
get_geo_collection(merge_join_col,'./datos/raster/Raster_test/', ['single_exctract_3'])

Exporting 1/1: ./datos/raster/Raster_test/single_exctract_3.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/fe855337f2dc555d471d13a880a83d94-dfa961c55c11e6b29323af7c1bee4c79:getPixels
Saving at : 
 ./datos/raster/Raster_test/single_exctract_3.tif
Fill values with Nan




Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


In [ ]:
geemap.ee_export_image( merge_join_col.first(), './datos/raster/Raster_test/2004_01_22_ZMVM.tif',  
                       region = ZM_table.geometry().bounds(),
                       unmask_value= -1000,
                      )

Generating URL ...
Please wait ...
Data downloaded to /mnt/HDD2/Cgeo/Contaminantes/pm-2.5_Drive/datos/raster/Raster_test/2004_01_22_ZMVM.tif


In [ ]:
merge_join_col.first()


In [ ]:
def add_ee_layer(self, ee_image_object, vis_params, name):
  map_id_dict = ee.Image(ee_image_object).getMapId(vis_params)
  folium.raster_layers.TileLayer(
      tiles=map_id_dict['tile_fetcher'].url_format,
      attr='Map Data &copy; <a href="https://earthengine.google.com/">Google Earth Engine</a>',
      name=name,
      overlay=True,
      control=True
  ).add_to(self)

In [ ]:
folium.Map.add_ee_layer = add_ee_layer

In [ ]:
vis_aod= {'bands':['dewpoint_temperature_2m'], 'min': 0,'max': 200,'palette':geemap.get_palette_colors('viridis') , 'opacity':0.95}

In [ ]:
map_fol = folium.Map()

map_fol.add_ee_layer(merge_join_col.first(), vis_aod ,'tonteria')

display(map_fol)


**SI funciona** 

El único problema es que al obtener las imágenes estas no contienen el nombre da cada banda, pero esto lo podemos arregrar directamente ya que se tenga. 


Hacemos una sóla función que baje todo el año y la zona metropolitana. 




In [ ]:
def get_year_zm(
        date_start_str,
        date_end_str,
        str_ZM,
        path_save,
        prefix = "aod_cli_"):
    
    """ The function will get all the data from the metropolitan area between
    the interval dates
    """
    dic_met_area = {
                    'ZMVM': "users/msalazar_cgeo/ZMVM",
                    'ZMG': "users/msalazar_cgeo/ZMG",
                    'ZMVT':"users/msalazar_cgeo/ZMVT",
                    'AMM': "users/msalazar_cgeo/AMM"}
    ZM_table = ee.FeatureCollection(dic_met_area[str_ZM])
    
    
    startdate_fun = ee.Date(date_start_str)
    enddate_fun = ee.Date(date_end_str)
    
    merge_join_col = get_image_range(startdate_fun, enddate_fun, ZM_table)
    
    list_dates = merge_join_col.aggregate_array('day').getInfo()

    name_dates_str = [ee.Date(i['value']).format('YYYY_MM_dd').getInfo() for i in list_dates]
    names_dates_str  = [prefix + str_ZM+ '_' + na for na in name_dates_str]
    print(names_dates_str)
    get_geo_collection(
        merge_join_col,
        path = path_save,
        file_names= names_dates_str,
        unmask_value= -100
    )
    
    return 

In [ ]:
def get_year_zm_no_resample(
        date_start_str,
        date_end_str,
        str_ZM,
        path_save,
        prefix = "aod_cli_"):
    
    """ The function will get all the data from the metropolitan area between
    the interval dates
    """
    dic_met_area = {
                    'ZMVM': "users/msalazar_cgeo/ZMVM",
                    'ZMG': "users/msalazar_cgeo/ZMG",
                    'ZMVT':"users/msalazar_cgeo/ZMVT",
                    'AMM': "users/msalazar_cgeo/AMM"}
    ZM_table = ee.FeatureCollection(dic_met_area[str_ZM])
    
    
    startdate_fun = ee.Date(date_start_str)
    enddate_fun = ee.Date(date_end_str)
    
    merge_join_col = get_image_range_no_resample(startdate_fun, enddate_fun, ZM_table)
    
    list_dates = merge_join_col.aggregate_array('day').getInfo()

    name_dates_str = [ee.Date(i['value']).format('YYYY_MM_dd').getInfo() for i in list_dates]
    names_dates_str  = [prefix + str_ZM+ '_' + na for na in name_dates_str]
    print(names_dates_str)
    get_geo_collection(
        merge_join_col,
        path = path_save,
        file_names= names_dates_str,
        unmask_value= -100
    )
    
    return 

In [ ]:
get_year_zm(
        "2005-01-01",
        "2005-07-01",
        "AMM",
        "./datos/raster/Raster_test/collection_test/2005/",
        prefix = "aod_cli_")

['aod_cli_AMM_2005_01_01', 'aod_cli_AMM_2005_01_02', 'aod_cli_AMM_2005_01_03', 'aod_cli_AMM_2005_01_04', 'aod_cli_AMM_2005_01_05', 'aod_cli_AMM_2005_01_06', 'aod_cli_AMM_2005_01_07', 'aod_cli_AMM_2005_01_08', 'aod_cli_AMM_2005_01_09', 'aod_cli_AMM_2005_01_10', 'aod_cli_AMM_2005_01_11', 'aod_cli_AMM_2005_01_12', 'aod_cli_AMM_2005_01_13', 'aod_cli_AMM_2005_01_14', 'aod_cli_AMM_2005_01_15', 'aod_cli_AMM_2005_01_16', 'aod_cli_AMM_2005_01_17', 'aod_cli_AMM_2005_01_18', 'aod_cli_AMM_2005_01_19', 'aod_cli_AMM_2005_01_20', 'aod_cli_AMM_2005_01_21', 'aod_cli_AMM_2005_01_22', 'aod_cli_AMM_2005_01_23', 'aod_cli_AMM_2005_01_24', 'aod_cli_AMM_2005_01_25', 'aod_cli_AMM_2005_01_26', 'aod_cli_AMM_2005_01_27', 'aod_cli_AMM_2005_01_28', 'aod_cli_AMM_2005_01_29', 'aod_cli_AMM_2005_01_30', 'aod_cli_AMM_2005_01_31', 'aod_cli_AMM_2005_02_01', 'aod_cli_AMM_2005_02_02', 'aod_cli_AMM_2005_02_03', 'aod_cli_AMM_2005_02_04', 'aod_cli_AMM_2005_02_05', 'aod_cli_AMM_2005_02_06', 'aod_cli_AMM_2005_02_07', 'aod_cli_AM

Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.




Exporting 2/181: ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_01_02.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/a97dbabf76019a1aea189ae9281ebccc-e7c9d22393d4ac15ceb985968db8a09d:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_01_02.tif
Fill values with Nan


Exporting 3/181: ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_01_03.tif


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/961e9f30e3421995f036b2baf2c001d5-ae8be4cff51dd0ecb598d3eafec8dcce:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_01_03.tif
Fill values with Nan


Exporting 4/181: ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_01_04.tif


...

Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.




Exporting 180/181: ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_06_29.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/000e08d3851fbe7f582078fa7be4cb1b-4400d1ca9f50390981ff789005647945:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_06_29.tif
Fill values with Nan


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.




Exporting 181/181: ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_06_30.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/8a35963157f1dcad68a392a023d1d108-8f9091cbf5cafa212e69e0ceeb621681:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2005/aod_cli_AMM_2005_06_30.tif
Fill values with Nan




Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


In [ ]:
get_year_zm(
        "2006-07-01",
        "2007-01-01",
        "AMM",
        "./datos/raster/Raster_test/collection_test/2006/",
        prefix = "aod_cli_")

['aod_cli_AMM_2006_07_01', 'aod_cli_AMM_2006_07_02', 'aod_cli_AMM_2006_07_03', 'aod_cli_AMM_2006_07_04', 'aod_cli_AMM_2006_07_05', 'aod_cli_AMM_2006_07_06', 'aod_cli_AMM_2006_07_07', 'aod_cli_AMM_2006_07_08', 'aod_cli_AMM_2006_07_09', 'aod_cli_AMM_2006_07_10', 'aod_cli_AMM_2006_07_11', 'aod_cli_AMM_2006_07_12', 'aod_cli_AMM_2006_07_13', 'aod_cli_AMM_2006_07_14', 'aod_cli_AMM_2006_07_15', 'aod_cli_AMM_2006_07_16', 'aod_cli_AMM_2006_07_17', 'aod_cli_AMM_2006_07_18', 'aod_cli_AMM_2006_07_19', 'aod_cli_AMM_2006_07_20', 'aod_cli_AMM_2006_07_21', 'aod_cli_AMM_2006_07_22', 'aod_cli_AMM_2006_07_23', 'aod_cli_AMM_2006_07_24', 'aod_cli_AMM_2006_07_25', 'aod_cli_AMM_2006_07_26', 'aod_cli_AMM_2006_07_27', 'aod_cli_AMM_2006_07_28', 'aod_cli_AMM_2006_07_29', 'aod_cli_AMM_2006_07_30', 'aod_cli_AMM_2006_07_31', 'aod_cli_AMM_2006_08_01', 'aod_cli_AMM_2006_08_02', 'aod_cli_AMM_2006_08_03', 'aod_cli_AMM_2006_08_04', 'aod_cli_AMM_2006_08_05', 'aod_cli_AMM_2006_08_06', 'aod_cli_AMM_2006_08_07', 'aod_cli_AM

Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.




Exporting 2/184: ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_07_02.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/3a6a141bf9fb5d602d3eb3a6ec586832-4322a6707fc4bb4d4c6f11ab97d0c2ae:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_07_02.tif
Fill values with Nan


Exporting 3/184: ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_07_03.tif


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/6f2f1db730bdf2939f68d47fd9ba39e9-7f69a7502c39a13e58cae42e31334f1c:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_07_03.tif
Fill values with Nan


Exporting 4/184: ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_07_04.tif


...

Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/c388c14baec4d593ad5fb915b819d07c-46d71712e549165d015f8ee98da143a7:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_12_30.tif
Fill values with Nan


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.




Exporting 184/184: ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_12_31.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/6a5292c7b8d6f514de17fda69e5ee9e1-509ad745108ed73eebeaecb76fa9324a:getPixels
Saving at : 
 ./datos/raster/Raster_test/collection_test/2006/aod_cli_AMM_2006_12_31.tif
Fill values with Nan




Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


In [ ]:
import rasterio
def set_band_names_gee(file_path):
    """Rename the bands in the file """
    dst_m= rasterio.open(file_path,'r+',  driver =  'GTiff')
    
    band_names = ["dewpoint_temperature_2m",
                  "total_evaporation",
                  "temperature_2m",
                  "total_precipitation_hourly",
                  "total_precipitation",
                  "relative_humidity",
                  "Optical_Depth_047",
                  "AOD_Uncertainty"]
    for num, band in enumerate(band_names ):
        dst_m.set_band_description(num+1, band)
    dst_m.close()


In [ ]:

def set_band_dir_gee(path_dir):
    files_li = os.listdir(path_dir)
    files_li = [fil for fil in files_li if fil[-4:] == ".tif" ]
    #files_li = [path_dir + '/'+fil for file in files_li]
    print("Changing file band names:")
    for fil in  files_li:
        set_band_names_gee(path_dir + '/'+fil)
    return
    

In [ ]:
ZM_str = "AMM"
path_zone= "./datos/raster/GEE_ZM/AMM_8_bands/"
for year in range(2008, 2023):
    get_year_zm(
        str(year) + "-01-01",
        str(year) + "-07-01",
        ZM_str,
        path_zone+str(year)+'/',
        prefix = "aod_cli_"
    )
    time.sleep(30) 
    get_year_zm(
        str(year) + "-07-01",
        str(year+1) + "-01-01",
        ZM_str,
        path_zone+str(year)+'/',
        prefix = "aod_cli_"
    )
#set_band_dir_gee("./datos/raster/AMM_8_bands/"+str(year)+'/')

['aod_cli_AMM_2008_01_01', 'aod_cli_AMM_2008_01_02', 'aod_cli_AMM_2008_01_03', 'aod_cli_AMM_2008_01_04', 'aod_cli_AMM_2008_01_05', 'aod_cli_AMM_2008_01_06', 'aod_cli_AMM_2008_01_07', 'aod_cli_AMM_2008_01_08', 'aod_cli_AMM_2008_01_09', 'aod_cli_AMM_2008_01_10', 'aod_cli_AMM_2008_01_11', 'aod_cli_AMM_2008_01_12', 'aod_cli_AMM_2008_01_13', 'aod_cli_AMM_2008_01_14', 'aod_cli_AMM_2008_01_15', 'aod_cli_AMM_2008_01_16', 'aod_cli_AMM_2008_01_17', 'aod_cli_AMM_2008_01_18', 'aod_cli_AMM_2008_01_19', 'aod_cli_AMM_2008_01_20', 'aod_cli_AMM_2008_01_21', 'aod_cli_AMM_2008_01_22', 'aod_cli_AMM_2008_01_23', 'aod_cli_AMM_2008_01_24', 'aod_cli_AMM_2008_01_25', 'aod_cli_AMM_2008_01_26', 'aod_cli_AMM_2008_01_27', 'aod_cli_AMM_2008_01_28', 'aod_cli_AMM_2008_01_29', 'aod_cli_AMM_2008_01_30', 'aod_cli_AMM_2008_01_31', 'aod_cli_AMM_2008_02_01', 'aod_cli_AMM_2008_02_02', 'aod_cli_AMM_2008_02_03', 'aod_cli_AMM_2008_02_04', 'aod_cli_AMM_2008_02_05', 'aod_cli_AMM_2008_02_06', 'aod_cli_AMM_2008_02_07', 'aod_cli_AM

Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/8870f717e10885c0d2bd905614916250-3d99a4c36c7d2f71ab5a85f5f6c259f3:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_01_02.tif
Fill values with Nan


Exporting 3/182: ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_01_03.tif


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/e0f31beb8113b22ebf25d3394d192cbd-91141c7f281e6def71623e9dec0e4086:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_01_03.tif
Fill values with Nan


Exporting 4/182: ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_01_04.tif


...

getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/630af44c8b529495a404386cc95474ad-214c4c3699c4729ac2c50f2c27d9fe39:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_05.tif
Fill values with Nan


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.




Exporting 37/182: ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_06.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/26b95bf0aa14a4ac8ec2ffa339858b35-344d087ad6778b27b030a8be89226737:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_06.tif
Fill values with Nan


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.
More than 1000 errors or warnings have been reported. No more will be reported from now.




Exporting 38/182: ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_07.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/be61edcf3f5ebd6000e68f00432b88d2-98c982d48bf0ce2cd86e307bfd9d3b6b:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_07.tif
Fill values with Nan


Exporting 39/182: ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_08.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/ace86e154d4203df377f68e39410ed6d-71701990058da90e6c6c3932d8c9d49e:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_08.tif
Fill values with Nan


Exporting 40/182: ./datos/raster/GEE_ZM/AMM_8_bands/2008/aod_cli_AMM_2008_02_09.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/b6e28cc891627d2d6422c47add12f274-0883c2c07fe394e8459e3be2edfc6216:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/

In [ ]:
get_year_zm(
        "2005-07-01",
        "2005-10-02",
        "AMM",
        path_zone+"2005"+'/',
        prefix = "aod_cli_"
)



['aod_cli_AMM_2005_07_01', 'aod_cli_AMM_2005_07_02', 'aod_cli_AMM_2005_07_03', 'aod_cli_AMM_2005_07_04', 'aod_cli_AMM_2005_07_05', 'aod_cli_AMM_2005_07_06', 'aod_cli_AMM_2005_07_07', 'aod_cli_AMM_2005_07_08', 'aod_cli_AMM_2005_07_09', 'aod_cli_AMM_2005_07_10', 'aod_cli_AMM_2005_07_11', 'aod_cli_AMM_2005_07_12', 'aod_cli_AMM_2005_07_13', 'aod_cli_AMM_2005_07_14', 'aod_cli_AMM_2005_07_15', 'aod_cli_AMM_2005_07_16', 'aod_cli_AMM_2005_07_17', 'aod_cli_AMM_2005_07_18', 'aod_cli_AMM_2005_07_19', 'aod_cli_AMM_2005_07_20', 'aod_cli_AMM_2005_07_21', 'aod_cli_AMM_2005_07_22', 'aod_cli_AMM_2005_07_23', 'aod_cli_AMM_2005_07_24', 'aod_cli_AMM_2005_07_25', 'aod_cli_AMM_2005_07_26', 'aod_cli_AMM_2005_07_27', 'aod_cli_AMM_2005_07_28', 'aod_cli_AMM_2005_07_29', 'aod_cli_AMM_2005_07_30', 'aod_cli_AMM_2005_07_31', 'aod_cli_AMM_2005_08_01', 'aod_cli_AMM_2005_08_02', 'aod_cli_AMM_2005_08_03', 'aod_cli_AMM_2005_08_04', 'aod_cli_AMM_2005_08_05', 'aod_cli_AMM_2005_08_06', 'aod_cli_AMM_2005_08_07', 'aod_cli_AM

In [ ]:
get_year_zm(
        "2005-10-04",
        "2006-01-01",
        "AMM",
        path_zone+"2005"+'/',
        prefix = "aod_cli_"
)

['aod_cli_AMM_2005_10_04', 'aod_cli_AMM_2005_10_05', 'aod_cli_AMM_2005_10_06', 'aod_cli_AMM_2005_10_07', 'aod_cli_AMM_2005_10_08', 'aod_cli_AMM_2005_10_09', 'aod_cli_AMM_2005_10_10', 'aod_cli_AMM_2005_10_11', 'aod_cli_AMM_2005_10_12', 'aod_cli_AMM_2005_10_13', 'aod_cli_AMM_2005_10_14', 'aod_cli_AMM_2005_10_15', 'aod_cli_AMM_2005_10_16', 'aod_cli_AMM_2005_10_17', 'aod_cli_AMM_2005_10_18', 'aod_cli_AMM_2005_10_19', 'aod_cli_AMM_2005_10_20', 'aod_cli_AMM_2005_10_21', 'aod_cli_AMM_2005_10_22', 'aod_cli_AMM_2005_10_23', 'aod_cli_AMM_2005_10_24', 'aod_cli_AMM_2005_10_25', 'aod_cli_AMM_2005_10_26', 'aod_cli_AMM_2005_10_27', 'aod_cli_AMM_2005_10_28', 'aod_cli_AMM_2005_10_29', 'aod_cli_AMM_2005_10_30', 'aod_cli_AMM_2005_10_31', 'aod_cli_AMM_2005_11_01', 'aod_cli_AMM_2005_11_02', 'aod_cli_AMM_2005_11_03', 'aod_cli_AMM_2005_11_04', 'aod_cli_AMM_2005_11_05', 'aod_cli_AMM_2005_11_06', 'aod_cli_AMM_2005_11_07', 'aod_cli_AMM_2005_11_08', 'aod_cli_AMM_2005_11_09', 'aod_cli_AMM_2005_11_10', 'aod_cli_AM

In [ ]:
get_year_zm(
        "2006-01-01",
        "2006-03-28",
        "AMM",
        path_zone+"2006"+'/',
        prefix = "aod_cli_"
)
get_year_zm(
        "2006-03-30",
        "2006-07-01",
        "AMM",
        path_zone+"2006"+'/',
        prefix = "aod_cli_"
)


['aod_cli_AMM_2006_01_01', 'aod_cli_AMM_2006_01_02', 'aod_cli_AMM_2006_01_03', 'aod_cli_AMM_2006_01_04', 'aod_cli_AMM_2006_01_05', 'aod_cli_AMM_2006_01_06', 'aod_cli_AMM_2006_01_07', 'aod_cli_AMM_2006_01_08', 'aod_cli_AMM_2006_01_09', 'aod_cli_AMM_2006_01_10', 'aod_cli_AMM_2006_01_11', 'aod_cli_AMM_2006_01_12', 'aod_cli_AMM_2006_01_13', 'aod_cli_AMM_2006_01_14', 'aod_cli_AMM_2006_01_15', 'aod_cli_AMM_2006_01_16', 'aod_cli_AMM_2006_01_17', 'aod_cli_AMM_2006_01_18', 'aod_cli_AMM_2006_01_19', 'aod_cli_AMM_2006_01_20', 'aod_cli_AMM_2006_01_21', 'aod_cli_AMM_2006_01_22', 'aod_cli_AMM_2006_01_23', 'aod_cli_AMM_2006_01_24', 'aod_cli_AMM_2006_01_25', 'aod_cli_AMM_2006_01_26', 'aod_cli_AMM_2006_01_27', 'aod_cli_AMM_2006_01_28', 'aod_cli_AMM_2006_01_29', 'aod_cli_AMM_2006_01_30', 'aod_cli_AMM_2006_01_31', 'aod_cli_AMM_2006_02_01', 'aod_cli_AMM_2006_02_02', 'aod_cli_AMM_2006_02_03', 'aod_cli_AMM_2006_02_04', 'aod_cli_AMM_2006_02_05', 'aod_cli_AMM_2006_02_06', 'aod_cli_AMM_2006_02_07', 'aod_cli_AM

In [ ]:
get_year_zm(
        "2022-07-01",
        "2022-07-12",
        "AMM",
        path_zone+"2022"+'/',
        prefix = "aod_cli_"
)
get_year_zm(
        "2022-07-16",
        "2023-01-01",
        "AMM",
        path_zone+"2022"+'/',
        prefix = "aod_cli_"
)

['aod_cli_AMM_2022_07_01', 'aod_cli_AMM_2022_07_02', 'aod_cli_AMM_2022_07_03', 'aod_cli_AMM_2022_07_04', 'aod_cli_AMM_2022_07_05', 'aod_cli_AMM_2022_07_06', 'aod_cli_AMM_2022_07_07', 'aod_cli_AMM_2022_07_08', 'aod_cli_AMM_2022_07_09', 'aod_cli_AMM_2022_07_10', 'aod_cli_AMM_2022_07_11']
Exporting 1/11: ./datos/raster/GEE_ZM/AMM_8_bands/2022/aod_cli_AMM_2022_07_01.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/a3270db6cce8698cb17036aa0512d4ab-e98e06648ebe65e73ed031d0ad824ef5:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2022/aod_cli_AMM_2022_07_01.tif
Fill values with Nan


Exporting 2/11: ./datos/raster/GEE_ZM/AMM_8_bands/2022/aod_cli_AMM_2022_07_02.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/6d003fafab5e61af77da7f85221af010-58a5ae037ca79193e305470de74cb1fb:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/AMM_8_bands/2022/aod_cli_AMM_2022_07_02.tif
Fill values with Nan


Exporti

In [ ]:
get_year_zm(
        "2007-07-01",
        "2008-01-01",
        "AMM",
        path_zone+"2007"+'/',
        prefix = "aod_cli_"
)

['aod_cli_AMM_2007_07_01', 'aod_cli_AMM_2007_07_02', 'aod_cli_AMM_2007_07_03', 'aod_cli_AMM_2007_07_04', 'aod_cli_AMM_2007_07_05', 'aod_cli_AMM_2007_07_06', 'aod_cli_AMM_2007_07_07', 'aod_cli_AMM_2007_07_08', 'aod_cli_AMM_2007_07_09', 'aod_cli_AMM_2007_07_10', 'aod_cli_AMM_2007_07_11', 'aod_cli_AMM_2007_07_12', 'aod_cli_AMM_2007_07_13', 'aod_cli_AMM_2007_07_14', 'aod_cli_AMM_2007_07_15', 'aod_cli_AMM_2007_07_16', 'aod_cli_AMM_2007_07_17', 'aod_cli_AMM_2007_07_18', 'aod_cli_AMM_2007_07_19', 'aod_cli_AMM_2007_07_20', 'aod_cli_AMM_2007_07_21', 'aod_cli_AMM_2007_07_22', 'aod_cli_AMM_2007_07_23', 'aod_cli_AMM_2007_07_24', 'aod_cli_AMM_2007_07_25', 'aod_cli_AMM_2007_07_26', 'aod_cli_AMM_2007_07_27', 'aod_cli_AMM_2007_07_28', 'aod_cli_AMM_2007_07_29', 'aod_cli_AMM_2007_07_30', 'aod_cli_AMM_2007_07_31', 'aod_cli_AMM_2007_08_01', 'aod_cli_AMM_2007_08_02', 'aod_cli_AMM_2007_08_03', 'aod_cli_AMM_2007_08_04', 'aod_cli_AMM_2007_08_05', 'aod_cli_AMM_2007_08_06', 'aod_cli_AMM_2007_08_07', 'aod_cli_AM

### Arreglar días faltantes.  

Se necesitan hacer los dias faltantes, el problema es que esos dias por alguna razón no tienen AOD. En la versión anterior se generaban sin problemas pero en mi versión no se pueden hacer. Los tengo que hacer manualmente para que el resto de los procesos se hagan. 






In [ ]:
startdate_fal = ee.Date("2005-10-03" )
enddate_fal = ee.Date("2005-10-04")
dic_met_area = {'ZMVM': "users/msalazar_cgeo/ZMVM",
                'ZMG': "users/msalazar_cgeo/ZMG",
                'ZMVT':"users/msalazar_cgeo/ZMVT",
                'AMM': "users/msalazar_cgeo/AMM"}
ZM_table = ee.FeatureCollection(dic_met_area['AMM'])
merge_dias_col_fal = get_image_range(startdate_fal, enddate_fal, ZM_table)

In [ ]:
prefix = "aod_cli_"
list_dates_fal = merge_dias_col_fal.aggregate_array('day').getInfo()
name_dates_fal = [ee.Date(i['value']).format('YYYY_MM_dd').getInfo() for i in list_dates_fal]
names_dates_fal  = [prefix + "AMM"+ '_' + na for na in name_dates_fal]

In [ ]:
names_dates_fal

['aod_cli_AMM_2005_10_03']

In [ ]:
list_ima_fal = merge_dias_col_fal.toList(2)
image_0 = ee.Image(list_ima_fal.get(0))
#image_1 = ee.Image(list_ima_fal.get(1))

In [ ]:
image_0

/home/miguel/miniconda3/envs/contaminantes/lib/python3.8/site-packages/eerepr/repr.py:57: UserWarning: Getting info failed with: 'Collection.toList: Error in map(ID=0_0):
Image.select: Pattern 'Optical_Depth_047' did not match any bands.'. Falling back to string repr.
  warn(f"Getting info failed with: '{e}'. Falling back to string repr.")


In [ ]:
# get_geo_tif(image_0,
#             './datos/raster/Raster_test/collection_test/2005/'+names_dates_fal[0],
#             unmask_val = -100, 
#             re_fill_nan = True,
#             timeout=300)
get_geo_tif(image_0,
            './datos/raster/Raster_test/collection_test/2005/'+names_dates_fal[0],
            unmask_val = -100, 
            re_fill_nan = True,
            url_params =  {
            'bands': [
              "dewpoint_temperature_2m",
              "total_evaporation",
              "temperature_2m",
              "total_precipitation_hourly",
              "total_precipitation",
              "relative_humidity",
            ],
            'format': "GEO_TIFF"
            },
            timeout=300)

An error occurred while downloading.
Collection.toList: Error in map(ID=0_0):
Image.select: Pattern 'Optical_Depth_047' did not match any bands.


In [ ]:
image_0.unmask(-100).getDownloadUrl({'format': "GEO_TIFF"})

EEException: Collection.toList: Error in map(ID=0_0):
Image.select: Pattern 'Optical_Depth_047' did not match any bands.

In [ ]:
get_geo_collection(
        merge_dias_col_fal,
        path = './datos/raster/Raster_test/collection_test/2005/',
        file_names= names_dates_fal,
        unmask_value= -100
    )


ee.ImageCollection({
  "functionInvocationValue": {
    "functionName": "Collection.map",
    "arguments": {
      "baseAlgorithm": {
        "functionDefinitionValue": {
          "argumentNames": [
            "_MAPPING_VAR_0_0"
          ],
          "body": {
            "functionInvocationValue": {
              "functionName": "Image.select",
              "arguments": {
                "bandSelectors": {
                  "constantValue": [
                    "dewpoint_temperature_2m",
                    "total_evaporation",
                    "temperature_2m",
                    "total_precipitation_hourly",
                    "total_precipitation",
                    "relative_humidity",
                    "Optical_Depth_047",
                    "AOD_Uncertainty",
                    "tonteria"
                  ]
                },
                "input": {
                  "argumentReference": "_MAPPING_VAR_0_0"
                }
              }
            }
     

In [ ]:
ZM_str = "ZMVT"
path_zone= "./datos/raster/GEE_ZM/ZMVT_8_bands/"
for year in range(2004, 2023):
    get_year_zm_no_resample(
        str(year) + "-01-01",
        str(year) + "-07-01",
        ZM_str,
        path_zone+str(year)+'/',
        prefix = "aod_cli_"
    )
    time.sleep(30) 
    get_year_zm_no_resample(
        str(year) + "-07-01",
        str(year+1) + "-01-01",
        ZM_str,
        path_zone+str(year)+'/',
        prefix = "aod_cli_"
    )
#set_band_dir_gee("./datos/raster/AMM_8_bands/"+str(year)+'/')

['aod_cli_ZMVT_2004_01_01', 'aod_cli_ZMVT_2004_01_02', 'aod_cli_ZMVT_2004_01_03', 'aod_cli_ZMVT_2004_01_04', 'aod_cli_ZMVT_2004_01_05', 'aod_cli_ZMVT_2004_01_06', 'aod_cli_ZMVT_2004_01_07', 'aod_cli_ZMVT_2004_01_08', 'aod_cli_ZMVT_2004_01_09', 'aod_cli_ZMVT_2004_01_10', 'aod_cli_ZMVT_2004_01_11', 'aod_cli_ZMVT_2004_01_12', 'aod_cli_ZMVT_2004_01_13', 'aod_cli_ZMVT_2004_01_14', 'aod_cli_ZMVT_2004_01_15', 'aod_cli_ZMVT_2004_01_16', 'aod_cli_ZMVT_2004_01_17', 'aod_cli_ZMVT_2004_01_18', 'aod_cli_ZMVT_2004_01_19', 'aod_cli_ZMVT_2004_01_20', 'aod_cli_ZMVT_2004_01_21', 'aod_cli_ZMVT_2004_01_22', 'aod_cli_ZMVT_2004_01_23', 'aod_cli_ZMVT_2004_01_24', 'aod_cli_ZMVT_2004_01_25', 'aod_cli_ZMVT_2004_01_26', 'aod_cli_ZMVT_2004_01_27', 'aod_cli_ZMVT_2004_01_28', 'aod_cli_ZMVT_2004_01_29', 'aod_cli_ZMVT_2004_01_30', 'aod_cli_ZMVT_2004_01_31', 'aod_cli_ZMVT_2004_02_01', 'aod_cli_ZMVT_2004_02_02', 'aod_cli_ZMVT_2004_02_03', 'aod_cli_ZMVT_2004_02_04', 'aod_cli_ZMVT_2004_02_05', 'aod_cli_ZMVT_2004_02_06', 

Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/af9feb81296ff9191cfa1608622cde4e-750c7457e65c8577b26a4e879069ea7d:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/ZMVT_8_bands/2004/aod_cli_ZMVT_2004_01_02.tif
Fill values with Nan


Exporting 3/182: ./datos/raster/GEE_ZM/ZMVT_8_bands/2004/aod_cli_ZMVT_2004_01_03.tif


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/d18149ca4c01c16f0c86d1d557aa85f6-206d73abd8f5b42b9c480dbced9b5c77:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/ZMVT_8_bands/2004/aod_cli_ZMVT_2004_01_03.tif
Fill values with Nan


Exporting 4/182: ./datos/raster/GEE_ZM/ZMVT_8_bands/2004/aod_cli_ZMVT_2004_01_04.tif


...

getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/322c194f394d83ad1751be7fc8794964-973efeeb4314e30261ebb36100c06fbe:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_07.tif
Fill values with Nan


Exporting 8/184: ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_08.tif


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/884d62c7703c3d95b3778672a31dda7d-eea7b87a0d9aedccbb1e18cbb5969304:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_08.tif
Fill values with Nan


Exporting 9/184: ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_09.tif


Warning 1: TIFFReadDirectory:Sum of Photometric type-related color channels and ExtraSamples doesn't match SamplesPerPixel. Defining non-color channels as ExtraSamples.
More than 1000 errors or warnings have been reported. No more will be reported from now.


getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/d010b0766a2d44abd260da8cf49349cc-43445b183fd7ccd40c985e899e67edea:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_09.tif
Fill values with Nan


Exporting 10/184: ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_10.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/fdb38f359e987b5d140942ac7bfb98d8-0fbb306ed17414e26599fd758ead4216:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_10.tif
Fill values with Nan


Exporting 11/184: ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_11.tif
getting url: 
 https://earthengine.googleapis.com/v1/projects/earthengine-legacy/thumbnails/e1e7c84b5d1b39bf783b51410ce939ee-f8783cef35eb0ddd7dc272b3cdfb6d12:getPixels
Saving at : 
 ./datos/raster/GEE_ZM/ZMVT_8_bands/2007/aod_cli_ZMVT_2007_07_11.tif
Fill values with Nan


Exporting

In [ ]:
ZM_str = "ZMG"
path_zone= "./datos/raster/GEE_ZM/ZMG_8_bands/"
for year in range(2004, 2023):
    get_year_zm(
        str(year) + "-01-01",
        str(year) + "-07-01",
        ZM_str,
        path_zone+str(year)+'/',
        prefix = "aod_cli_"
    )
    time.sleep(30) 
    get_year_zm(
        str(year) + "-07-01",
        str(year+1) + "-01-01",
        ZM_str,
        path_zone+str(year)+'/',
        prefix = "aod_cli_"
    )
#set_band_dir_gee("./datos/raster/AMM_8_bands/"+str(year)+'/')